In [1]:
import pandas as pd
import geopandas as gpd
import folium
from folium import plugins
import branca
import time
start_time = time.time()

In [2]:
## Load encoded restaurant license data
dc_food = pd.read_csv("DC_FoodEstablish_Since2005.csv", low_memory = False)
dc_rest = dc_food[(dc_food.LICENSE_END_DATE >= '2018-01-01') 
                  & (dc_food.LICENSECATEGORY.isin(['Restaurant','Delicatessen']))
                 ].copy()

## Load neighborhood areas
dc_neighborhood_area = pd.read_csv("neigbh_area.csv", low_memory = False)

## Load geojson as geopandas dataframe
dc_zil_gdf = gpd.read_file("zillow_nb_dc.geojson")    

dc_zil_gdf.head()

city                      name regionid                county state  \
0  Washington       Catholic University   273159  District of Columbia    DC   
1  Washington            McLean Gardens   121759  District of Columbia    DC   
2  Washington             Benning Ridge   403493  District of Columbia    DC   
3  Washington  Southwest Federal Center   403489  District of Columbia    DC   
4  Washington          Civic Betterment   403495  District of Columbia    DC   

                                            geometry  
0  POLYGON ((-77.00433078657653 38.94064135955279...  
1  POLYGON ((-77.07520122673562 38.93977423544837...  
2  POLYGON ((-76.93492799998681 38.87296000008542...  
3  POLYGON ((-77.01608829199994 38.88757112300004...  
4  POLYGON ((-76.9305251833312 38.88062151833325,...

# 2.3a Calculate Summary Metrics

In [3]:
## Returns 1 if license is active during time period of interest and specified category
def active(col1, col2, col3, col4, license, date):
    if (col1 == 'Ready to Renew' or col1 == 'Active') and col2 >= date and col3 <= date and col4 == license:
        return 1
    else:
        return 0  
    
## Returns 1 if license is not active, license is within time period of interest and license is specified category

def closed(col1, col2, col3, license, end, start):
    if col1 != 'Ready to Renew' and col1 != 'Active' and col2 <= end and col2 >= start and col3 == license:
        return 1
    else:
        return 0   

In [4]:
## Apply functions to create columns for restaurants and delis
dc_rest['active_rest'] = dc_rest.apply(lambda x: active(x['LICENSESTATUS'],x['LICENSE_END_DATE'],x['LICENSE_START_DATE'],x['LICENSECATEGORY'],'Restaurant', '2019-09-01'), axis = 1)
dc_rest['close_18_rest'] = dc_rest.apply(lambda x: closed(x['LICENSESTATUS'],x['LICENSE_END_DATE'],x['LICENSECATEGORY'],'Restaurant', '2018-12-31', '2017-12-31'), axis = 1)
dc_rest['close_19_rest'] = dc_rest.apply(lambda x: closed(x['LICENSESTATUS'],x['LICENSE_END_DATE'],x['LICENSECATEGORY'],'Restaurant', '2019-12-31', '2018-12-31'), axis = 1)

dc_rest['active_deli'] = dc_rest.apply(lambda x: active(x['LICENSESTATUS'],x['LICENSE_END_DATE'],x['LICENSE_START_DATE'],x['LICENSECATEGORY'],'Delicatessen', '2019-09-01'), axis = 1)
dc_rest['close_18_deli'] = dc_rest.apply(lambda x: closed(x['LICENSESTATUS'],x['LICENSE_END_DATE'],x['LICENSECATEGORY'],'Delicatessen', '2018-12-31', '2017-12-31'), axis = 1)
dc_rest['close_19_deli'] = dc_rest.apply(lambda x: closed(x['LICENSESTATUS'],x['LICENSE_END_DATE'],x['LICENSECATEGORY'],'Delicatessen', '2019-12-31', '2018-12-31'), axis = 1)


In [5]:
## Roll-up the data to the neighborhood level
dc_rest_grp = dc_rest.groupby("neighborhood")['active_rest','close_18_rest','close_19_rest','active_deli','close_18_deli','close_19_deli'].sum()

## Create a couple of additional counts
dc_rest_grp['active_tot'] = dc_rest_grp['active_rest'] + dc_rest_grp['active_deli']
dc_rest_grp['close_18_tot'] = dc_rest_grp['close_18_rest'] + dc_rest_grp['close_18_deli']
dc_rest_grp['close_19_tot'] = dc_rest_grp['close_19_rest'] + dc_rest_grp['close_19_deli']
dc_rest_grp['pct_closed_rest'] = 100*round((dc_rest_grp['close_19_rest'] + dc_rest_grp['close_18_rest'])/(dc_rest_grp['close_19_rest'] + dc_rest_grp['close_18_rest']+dc_rest_grp['active_rest']),3)
dc_rest_grp['pct_closed_deli'] = 100*round((dc_rest_grp['close_19_deli'] + dc_rest_grp['close_18_deli'])/(dc_rest_grp['close_19_deli'] + dc_rest_grp['close_18_deli']+dc_rest_grp['active_deli']),3)
dc_rest_grp['pct_closed_tot'] = 100*round((dc_rest_grp['close_19_tot'] + dc_rest_grp['close_18_tot'])/(dc_rest_grp['close_19_tot'] + dc_rest_grp['close_18_tot']+dc_rest_grp['active_tot']),3)

## Replace NAs with 0
dc_rest_grp.fillna(0, inplace = True)

dc_rest_grp.head()

active_rest  close_18_rest  \
neighborhood                                                                   
Adams Morgan                                               83             16   
American University Park                                   26              3   
Anacostia                                                   1              0   
Anacostia Naval Station - Boiling Air Force Base            1              0   
Arboretum                                                   0              0   

                                                  close_19_rest  active_deli  \
neighborhood                                                                   
Adams Morgan                                                  9           19   
American University Park                                      1            5   
Anacostia                                                     0            6   
Anacostia Naval Station - Boiling Air Force Base              0            1   
Arboretum                                                     0            1   

                                                  close_18_deli  \
neighborhood                                                      
Adams Morgan                                                  3   
American University Park                                      0   
Anacostia                                                     1   
Anacostia Naval Station - Boiling Air Force Base              0   
Arboretum                                                     0   

                                                  close_19_deli  active_tot  \
neighborhood                                                                  
Adams Morgan                                                  3         102   
American University Park                                      0          31   
Anacostia                                                     3           7   
Anacostia Naval Station - Boiling Air Force Base              0           2   
Arboretum                                                     2           1   

                                                  close_18_tot  close_19_tot  \
neighborhood                                                                   
Adams Morgan                                                19            12   
American University Park                                     3             1   
Anacostia                                                    1             3   
Anacostia Naval Station - Boiling Air Force Base             0             0   
Arboretum                                                    0             2   

                                                  pct_closed_rest  \
neighborhood                                                        
Adams Morgan                                                 23.1   
American University Park                                     13.3   
Anacostia                                                     0.0   
Anacostia Naval Station - Boiling Air Force Base              0.0   
Arboretum                                                     0.0   

                                                  pct_closed_deli  \
neighborhood                                                        
Adams Morgan                                                 24.0   
American University Park                                      0.0   
Anacostia                                                    40.0   
Anacostia Naval Station - Boiling Air Force Base              0.0   
Arboretum                                                    66.7   

                                                  pct_closed_tot  
neighborhood                                                      
Adams Morgan                                                23.3  
American University Park                                    11.4  
Anacostia                                                   36.4  
Anacostia Naval Station - Boiling Air Fo

In [6]:
### If number of food establishments is less than 5, 0 out the percent closed metric
def min_limit(col1, col2):
    if col1 <= 5:
        return 0
    else:
        return col2
    
dc_rest_grp['pct_closed_tot'] = dc_rest_grp.apply(lambda x: min_limit(x['active_tot'],x['pct_closed_tot']), axis = 1)
dc_rest_grp['pct_closed_rest'] = dc_rest_grp.apply(lambda x: min_limit(x['active_rest'],x['pct_closed_rest']), axis = 1)
dc_rest_grp['pct_closed_deli'] = dc_rest_grp.apply(lambda x: min_limit(x['active_deli'],x['pct_closed_deli']), axis = 1)

dc_rest_grp.head()

active_rest  close_18_rest  \
neighborhood                                                                   
Adams Morgan                                               83             16   
American University Park                                   26              3   
Anacostia                                                   1              0   
Anacostia Naval Station - Boiling Air Force Base            1              0   
Arboretum                                                   0              0   

                                                  close_19_rest  active_deli  \
neighborhood                                                                   
Adams Morgan                                                  9           19   
American University Park                                      1            5   
Anacostia                                                     0            6   
Anacostia Naval Station - Boiling Air Force Base              0            1   
Arboretum                                                     0            1   

                                                  close_18_deli  \
neighborhood                                                      
Adams Morgan                                                  3   
American University Park                                      0   
Anacostia                                                     1   
Anacostia Naval Station - Boiling Air Force Base              0   
Arboretum                                                     0   

                                                  close_19_deli  active_tot  \
neighborhood                                                                  
Adams Morgan                                                  3         102   
American University Park                                      0          31   
Anacostia                                                     3           7   
Anacostia Naval Station - Boiling Air Force Base              0           2   
Arboretum                                                     2           1   

                                                  close_18_tot  close_19_tot  \
neighborhood                                                                   
Adams Morgan                                                19            12   
American University Park                                     3             1   
Anacostia                                                    1             3   
Anacostia Naval Station - Boiling Air Force Base             0             0   
Arboretum                                                    0             2   

                                                  pct_closed_rest  \
neighborhood                                                        
Adams Morgan                                                 23.1   
American University Park                                     13.3   
Anacostia                                                     0.0   
Anacostia Naval Station - Boiling Air Force Base              0.0   
Arboretum                                                     0.0   

                                                  pct_closed_deli  \
neighborhood                                                        
Adams Morgan                                                 24.0   
American University Park                                      0.0   
Anacostia                                                    40.0   
Anacostia Naval Station - Boiling Air Force Base              0.0   
Arboretum                                                     0.0   

                                                  pct_closed_tot  
neighborhood                                                      
Adams Morgan                                                23.3  
American University Park                                    11.4  
Anacostia                                                   36.4  
Anacostia Naval Station - Boiling Air Fo

# 2.3b Create GeoPandas Dataframe

In [7]:
### merge the variables of interest into the Geodataframe
dc_gdf = dc_zil_gdf.merge(dc_rest_grp, left_on='name', right_on='neighborhood', how='left').fillna(0)

### merge the area of each neighborhood
dc_gdf = dc_gdf.merge(dc_neighborhood_area)
dc_gdf.head()

city                      name regionid                county state  \
0  Washington       Catholic University   273159  District of Columbia    DC   
1  Washington            McLean Gardens   121759  District of Columbia    DC   
2  Washington             Benning Ridge   403493  District of Columbia    DC   
3  Washington  Southwest Federal Center   403489  District of Columbia    DC   
4  Washington          Civic Betterment   403495  District of Columbia    DC   

                                            geometry  active_rest  \
0  POLYGON ((-77.00433078657653 38.94064135955279...         14.0   
1  POLYGON ((-77.07520122673562 38.93977423544837...          0.0   
2  POLYGON ((-76.93492799998681 38.87296000008542...          1.0   
3  POLYGON ((-77.01608829199994 38.88757112300004...         34.0   
4  POLYGON ((-76.9305251833312 38.88062151833325,...          0.0   

   close_18_rest  close_19_rest  active_deli  close_18_deli  close_19_deli  \
0            1.0            1.0          7.0            1.0            2.0   
1            0.0            0.0          0.0            0.0            0.0   
2            1.0            0.0          0.0            0.0            1.0   
3            2.0            1.0         11.0            0.0            3.0   
4            0.0            0.0          3.0            2.0            1.0   

   active_tot  close_18_tot  close_19_tot  pct_closed_rest  pct_closed_deli  \
0        21.0           2.0           3.0             12.5             30.0   
1         0.0           0.0           0.0              0.0              0.0   
2         1.0           1.0           1.0              0.0              0.0   
3        45.0           2.0           4.0              8.1             21.4   
4         3.0           2.0           1.0              0.0              0.0   

   pct_closed_tot     sq_mi  
0            19.2  2.263850  
1             0.0  0.190896  
2             0.0  0.837476  
3            11.8  0.743870  
4             0.0  0.117713

In [8]:
## create function that calculate the number of establishments per square mile
def sq_mi(col1,col2):
    if col1 == 0:
        return 0
    else:
        return round(col1/col2,0)
    
dc_gdf['active_tot_sq_mi'] = dc_gdf.apply(lambda x: sq_mi(x['active_tot'],x['sq_mi']), axis = 1)      
dc_gdf['active_rest_sq_mi'] = dc_gdf.apply(lambda x: sq_mi(x['active_rest'],x['sq_mi']), axis=1)      
dc_gdf['active_deli_sq_mi'] = dc_gdf.apply(lambda x: sq_mi(x['active_deli'],x['sq_mi']), axis=1)      

dc_gdf.head()

city                      name regionid                county state  \
0  Washington       Catholic University   273159  District of Columbia    DC   
1  Washington            McLean Gardens   121759  District of Columbia    DC   
2  Washington             Benning Ridge   403493  District of Columbia    DC   
3  Washington  Southwest Federal Center   403489  District of Columbia    DC   
4  Washington          Civic Betterment   403495  District of Columbia    DC   

                                            geometry  active_rest  \
0  POLYGON ((-77.00433078657653 38.94064135955279...         14.0   
1  POLYGON ((-77.07520122673562 38.93977423544837...          0.0   
2  POLYGON ((-76.93492799998681 38.87296000008542...          1.0   
3  POLYGON ((-77.01608829199994 38.88757112300004...         34.0   
4  POLYGON ((-76.9305251833312 38.88062151833325,...          0.0   

   close_18_rest  close_19_rest  active_deli  ...  active_tot  close_18_tot  \
0            1.0            1.0          7.0  ...        21.0           2.0   
1            0.0            0.0          0.0  ...         0.0           0.0   
2            1.0            0.0          0.0  ...         1.0           1.0   
3            2.0            1.0         11.0  ...        45.0           2.0   
4            0.0            0.0          3.0  ...         3.0           2.0   

   close_19_tot  pct_closed_rest  pct_closed_deli  pct_closed_tot     sq_mi  \
0           3.0             12.5             30.0            19.2  2.263850   
1           0.0              0.0              0.0             0.0  0.190896   
2           1.0              0.0              0.0             0.0  0.837476   
3           4.0              8.1             21.4            11.8  0.743870   
4           1.0              0.0              0.0             0.0  0.117713   

   active_tot_sq_mi  active_rest_sq_mi  active_deli_sq_mi  
0               9.0                6.0                3.0  
1               0.0                0.0                0.0  
2               1.0                1.0                0.0  
3              60.0               46.0               15.0  
4              25.0                0.0               25.0  

[5 rows x 22 columns]

# 3.1 Initiate the Map

In [9]:
centroid=dc_gdf.geometry.centroid ## identifies the center point of all the neighborhood shapes 

m=folium.Map(location=[centroid.y.mean(), centroid.x.mean()], zoom_start=12) ## initiaes a map based on the centroid
    
m

In [10]:
variable = 'active_rest' #active restaurants in Washington, DC as of 9/2019
name = '# Active Restaurants'

print(name, "colorscale")
print("Min:",dc_gdf[variable].min())
print("Max:",dc_gdf[variable].max())
    
colorscale = branca.colormap.linear.YlOrRd_09.scale(dc_gdf[variable].min(), dc_gdf[variable].max()) 
colorscale

# Active Restaurants colorscale
Min: 0.0
Max: 294.0


In [11]:
# create df with neighborhood name and variable of interest, sorted from largest to smallest
df = dc_gdf[['name', variable]].sort_values(by = variable, ascending = False) 
    
# reset index so that the largest value corresponds to row 0 and smallest to row 136
df.reset_index(inplace = True)
leg_brks = list(df[df.index.isin([0,4,9,19,29,49])][variable]) # identify the value of the var by index position
    
# make the smallest value of the scale be 0
leg_brks.append(0)
leg_brks.sort() # sort from smallest to largest
print("Quantiles:", leg_brks)
    

Quantiles: [0, 6.0, 16.0, 27.0, 64.0, 104.0, 294.0]


In [12]:
print(name, "colorscale")

colorscale = branca.colormap.linear.YlOrRd_09.scale(dc_gdf[variable].min(), dc_gdf[variable].max()) 
colorscale = colorscale.to_step(n = 6, quantiles = leg_brks) ## sets quantile breaks 
colorscale.caption = name ## adds name for legend
    
colorscale

# Active Restaurants colorscale


In [13]:
variable = 'active_rest' #active restaurants in Washington, DC as of 9/2019
name = '# Active Restaurants'

folium.GeoJson(dc_gdf, ## GeoPandas dataframe
               name="Washington DC",
                   
               ## controls the fill of the geo regions; applying colorscale based on variable
               style_function=lambda x: {"weight":1
                                         , 'color': '#545453'
                                         ## if variable is 0 map is a very light grey
                                         ## else colorscale applies based on variable
                                         , 'fillColor':'#9B9B9B' if x['properties'][variable] == 0 
                                         else colorscale(x['properties'][variable])
                                         ## similarly opacity is increased if value is 0
                                         , 'fillOpacity': 0.2 if x['properties'][variable] == 0 
                                         else 0.5},
                   
               ## changes styling of geo regions upon hover
               highlight_function=lambda x: {'weight':3, 'color':'black', 'fillOpacity': 1}, 
               
                ## tooltip can include information from any column in the GeoPandas dataframe   
                tooltip=folium.features.GeoJsonTooltip(
                fields=['name', 'active_tot', 'active_tot_sq_mi', variable],
                aliases=['Neighborhood:', '# Active Restaurants + Delis:', '# Active Per Sq Mi', name])
              ).add_to(m)

## add colorscale to map so that it appears as the legend
colorscale.add_to(m)
    
m

In [14]:
def dc_map(variable, name):
    
    ###################################################################
    ### 3.1 Initiate the map
    ###################################################################
    
    centroid=dc_gdf.geometry.centroid ## identifies the center point of all the neighborhood shapes 

    m=folium.Map(location=[centroid.y.mean(), centroid.x.mean()], zoom_start=12) ## initiaes a map based on the centroid
    
    ###################################################################
    ### Creating the breaks for the colorscale
    ###################################################################
    
    # create df with neighborhood name and variable of interest, sorted from largest to smallest
    df = dc_gdf[['name', variable]].sort_values(by = variable, ascending = False) 
    
    # reset index so that the largest value corresponds to row 0 and smallest to row 136
    df.reset_index(inplace = True)
    leg_brks = list(df[df.index.isin([0,4,9,19,29,49])][variable]) # identify the value of the var by index position
    
    # make the smallest value of the scale be 0
    leg_brks.append(0)
    leg_brks.sort() # sort from smallest to largest
 
    ###################################################################
    ### 3.2 Creating the colormap
    ###################################################################
 
    # sets coloring scale range to variable min and max
    colorscale = branca.colormap.linear.YlOrRd_09.scale(dc_gdf[variable].min(), dc_gdf[variable].max()) 
    colorscale = colorscale.to_step(n = 6, quantiles = leg_brks) ## sets quantile breaks 
    colorscale.caption = name ## adds name for legend

    ###################################################################
    ### 3.3 Folium GeoJson Class
    ###################################################################
    
    folium.GeoJson(dc_gdf, ## GeoPandas dataframe
               name="Washington DC",
                   
               ## controls the fill of the geo regions; applying colorscale based on variable
               style_function=lambda x: {"weight":1
                                         , 'color': '#545453'
                                        # this looks up name of neighborhood in GeoJSON and colors
                                        # based on the value of the variable we're plotting
                                         , 'fillColor':'#9B9B9B' if x['properties'][variable] == 0 
                                         else colorscale(x['properties'][variable])
                                         ## similarly opacity is increased if value is 0
                                         , 'fillOpacity': 0.2 if x['properties'][variable] == 0 
                                         else 0.5},
                   
               ## changes styling of geo regions upon hover
               highlight_function=lambda x: {'weight':3, 'color':'black', 'fillOpacity': 1}, 
               
                ## tooltip can include information from any column in the GeoPandas dataframe   
                tooltip=folium.features.GeoJsonTooltip(
                fields=['name', 'active_tot', 'active_tot_sq_mi', variable],
                aliases=['Neighborhood:', '# Active Restaurants + Delis:', '# Active Per Sq Mi', name])
              ).add_to(m)

    ## add colorscale to map so that it appears as the legend
    colorscale.add_to(m)
    
    return m

In [15]:
dc_map('active_rest_sq_mi', '# Active rest per sq')

In [16]:
dc_map('pct_closed_rest', 'Pct Closed:')

In [17]:
(time.time() - start_time)/60

0.06354333559672037